<a href="https://colab.research.google.com/github/merucode/RL/blob/93-Project-Trader-Custom_enviromnet/02_Reinforce.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Install Dependency and Test

In [1]:
!git clone -b 93-Project-Trader-Custom_enviromnet https://github.com/merucode/RL.git
!cd RL && mv * ../

Cloning into 'RL'...
remote: Enumerating objects: 216, done.
remote: Counting objects: 100% (136/136), done.
remote: Compressing objects: 100% (135/135), done.
remote: Total 216 (delta 55), reused 0 (delta 0), pack-reused 80
Receiving objects: 100% (216/216), 11.50 MiB | 5.64 MiB/s, done.
Resolving deltas: 100% (82/82), done.


In [22]:
!pip install gym==0.25.2
!pip install -e gym-examples

Obtaining file:///content/gym-examples
  Preparing metadata (setup.py) ... done
  Attempting uninstall: gym-examples
    Found existing installation: gym-examples 0.0.1
    Uninstalling gym-examples-0.0.1:
      Successfully uninstalled gym-examples-0.0.1
  Running setup.py develop for gym-examples


### NOTE: After inistall gym-examples, Restart runtime

# STEP. Ready Data

In [1]:
import pandas as pd

df1 = pd.read_csv('KRW-BTC_5m_171001_200903_upbit.csv')
df2 = pd.read_csv('KRW-BTC_5m_200904_230810_upbit.csv')

df = pd.concat([df1, df2], ignore_index=True)
df = df[df.columns[1:]]
print(df)

              open        high         low       close    volume
0        4797000.0   4800000.0   4793000.0   4800000.0  0.013444
1        4798000.0   4799000.0   4792000.0   4793000.0  0.013597
2        4795000.0   4802000.0   4795000.0   4795000.0  0.016304
3        4801000.0   4802000.0   4795000.0   4801000.0  0.017136
4        4797000.0   4799000.0   4791000.0   4799000.0  0.007615
...            ...         ...         ...         ...       ...
492907  39205000.0  39208000.0  39179000.0  39206000.0  2.508436
492908  39206000.0  39212000.0  39186000.0  39212000.0  1.350777
492909  39190000.0  39231000.0  39190000.0  39212000.0  2.929709
492910  39212000.0  39214000.0  39188000.0  39191000.0  3.407502
492911  39191000.0  39210000.0  39188000.0  39188000.0  3.884740

[492912 rows x 5 columns]


In [2]:
# Preporcessing
df = df[:3000] #Temp : TEST
df_render = df
print(df)

           open       high        low      close    volume
0     4797000.0  4800000.0  4793000.0  4800000.0  0.013444
1     4798000.0  4799000.0  4792000.0  4793000.0  0.013597
2     4795000.0  4802000.0  4795000.0  4795000.0  0.016304
3     4801000.0  4802000.0  4795000.0  4801000.0  0.017136
4     4797000.0  4799000.0  4791000.0  4799000.0  0.007615
...         ...        ...        ...        ...       ...
2995  6442000.0  6457000.0  6442000.0  6442000.0  0.008992
2996  6431000.0  6431000.0  6426000.0  6426000.0  0.009791
2997  6465000.0  6465000.0  6378000.0  6427000.0  0.865518
2998  6353000.0  6387000.0  6353000.0  6359000.0  0.131957
2999  6387000.0  6474000.0  6376000.0  6474000.0  0.147008

[3000 rows x 5 columns]


In [3]:
df_ohlc = df[df.columns[:4]]
df_ohlc_normalization = (df_ohlc - df_ohlc.mean())/df_ohlc.std()
df_v = df[df.columns[-1:]]
df_v_normalization =  (df_v - df_v.mean())/df_v.std()
df = pd.concat([df_ohlc_normalization, df_v_normalization], axis=1)
print(df)

          open      high       low     close    volume
0    -0.998907 -1.017551 -0.981455 -0.991536 -0.099985
1    -0.996558 -1.019882 -0.983816 -1.007926 -0.099811
2    -1.003604 -1.012889 -0.976733 -1.003243 -0.096738
3    -0.989512 -1.012889 -0.976733 -0.989194 -0.095794
4    -0.998907 -1.019882 -0.986177 -0.993877 -0.106601
...        ...       ...       ...       ...       ...
2995  2.864635  2.844702  2.911621  2.853247 -0.105038
2996  2.838799  2.784099  2.873847  2.815783 -0.104131
2997  2.918654  2.863349  2.760525  2.818124  0.867208
2998  2.655604  2.681541  2.701503  2.658901  0.034540
2999  2.735458  2.884327  2.755803  2.928176  0.051624

[3000 rows x 5 columns]


### Check env

In [4]:
import time
import matplotlib.pyplot as plt
import gym
import numpy as np

In [4]:
env = gym.make("gym_examples:TradeWorld-v0", df=df, obs_len=180)

# single env
print(f'observation space : {env.observation_space}')
print(f'action space      : {env.action_space}')
print(f'observation shape : {env.observation_space.shape[0]}')
print(f'action shape      : {env.action_space.n}')

obs = env.reset()
action = 10
env.step(action)

observation space : Box(0.0, inf, (900,), float64)
action space      : Discrete(12)
observation shape : 900
action shape      : 12


/usr/local/lib/python3.10/dist-packages/gym/core.py:317: DeprecationWarning: WARN: Initializing wrapper in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(
/usr/local/lib/python3.10/dist-packages/gym/wrappers/step_api_compatibility.py:39: DeprecationWarning: WARN: Initializing environment in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(
/usr/local/lib/python3.10/dist-packages/gym/utils/passive_env_checker.py:141: UserWarning: WARN: The obs returned by the `reset()` method was expecting numpy array dtype to be float64, actual type: float32
  logger.warn(
/usr/local/lib/python3.10/dist-packages/gym/utils/passive_env_checker.py:141: UserWarning: WARN: The obs returned by the `step()` method was expecting numpy array dtype to be fl

(array([4.7970001e+02, 4.8000000e+02, 4.7929999e+02, 4.8000000e+02,
        1.3444000e-02, 4.7979999e+02, 4.7989999e+02, 4.7920001e+02,
        4.7929999e+02, 1.3597000e-02, 4.7950000e+02, 4.8020001e+02,
        4.7950000e+02, 4.7950000e+02, 1.6303999e-02, 4.8010001e+02,
        4.8020001e+02, 4.7950000e+02, 4.8010001e+02, 1.7136000e-02,
        4.7970001e+02, 4.7989999e+02, 4.7910001e+02, 4.7989999e+02,
        7.6150000e-03, 4.8010001e+02, 4.8029999e+02, 4.8010001e+02,
        4.8020001e+02, 9.0269996e-03, 4.8010001e+02, 4.8029999e+02,
        4.7970001e+02, 4.8029999e+02, 7.8130001e-03, 4.8079999e+02,
        4.8139999e+02, 4.8020001e+02, 4.8020001e+02, 2.8278539e-01,
        4.8020001e+02, 4.8089999e+02, 4.7979999e+02, 4.8029999e+02,
        2.1795999e-02, 4.8070001e+02, 4.8150000e+02, 4.8070001e+02,
        4.8100000e+02, 1.2361000e-02, 4.8100000e+02, 4.8100000e+02,
        4.7979999e+02, 4.8039999e+02, 1.0418000e-02, 4.8029999e+02,
        4.8139999e+02, 4.8029999e+02, 4.8139999e

In [5]:
envs = gym.vector.make("gym_examples:TradeWorld-v0", num_envs=2, df=df, obs_len=180)
obs_b = envs.reset()
actions = np.array([10, 5])
envs.step(actions)

/usr/local/lib/python3.10/dist-packages/gym/vector/vector_env.py:56: DeprecationWarning: WARN: Initializing vector env in old step API which returns one bool array instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(


(array([[4.79700012e+02, 4.80000000e+02, 4.79299988e+02, ...,
         4.86899994e+02, 4.86899994e+02, 3.99495155e-01],
        [4.79700012e+02, 4.80000000e+02, 4.79299988e+02, ...,
         4.86899994e+02, 4.86899994e+02, 3.99495155e-01]]),
 array([0.7, 0.2]),
 array([False, False]),
 {'balance': array([1000.7, 1000.2]), '_balance': array([ True,  True])})

In [ ]:
# def create_env(env_name, num_envs):
#     env = gym.vector.make(env_name, num_envs=num_envs, df=df, obs_len=180)
#     env = RecordEpisodeStatistics(env)
#     #env = NormalizeObservation(env)  # Not use : Because of volume colume, It is not working well
#     env = NormalizeReward(env)
#     return env

# STEP. Reinforce

In [4]:
import gym
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.distributions import Categorical
import numpy as np

#Device
device = device = 'cuda' if torch.cuda.is_available() else 'cpu'

#Hyperparameters
learning_rate = 0.0002
gamma         = 0.98

class Policy(nn.Module):
    def __init__(self):
        super(Policy, self).__init__()
        self.data = []

        self.fc1 = nn.Linear(900, 128)
        self.fc2 = nn.Linear(128, 128)
        self.fc3 = nn.Linear(128, 12)
        self.optimizer = optim.Adam(self.parameters(), lr=learning_rate)

    def forward(self, x):
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = F.softmax(self.fc3(x), dim=0)
        return x

    def put_data(self, item):
        self.data.append(item)

    def train_net(self):
        R = 0
        self.optimizer.zero_grad()
        for r, prob in self.data[::-1]:
            R = r + gamma * R
            loss = -torch.log(prob) * R
            loss.backward()
        self.optimizer.step()
        self.data = []

In [5]:
import random

def action_eps(action, eps):
    coin = random.random()
    if coin < eps:
        action_e = random.randint(0,11)
    else:
        action_e = action
    return action_e

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [11]:
def main():
    env = gym.make("gym_examples:TradeWorld-v0", df=df, obs_len=180)
    pi = Policy()
    score = 0.0
    max_avg_score = -2000.0
    print_interval = 10
    eps = 0.5
    pi.to(device)

    for n_epi in range(3000):
        s = env.reset()
        done = False

        while not done:
            prob = pi(torch.from_numpy(s).float().to(device))
            m = Categorical(prob)

            a = m.sample()
            a = action_eps(a.item(),eps)
            a = torch.tensor(a)
            s_prime, r, done, info = env.step(a.item())
            pi.put_data((r,prob[a]))
            s = s_prime
            score += r
            #print(f"DEBUG action: {a.item()}")
            #print(f"DEBUG reward: {r}")

        pi.train_net()

        if n_epi%print_interval==0 and n_epi!=0:
            print("# of episode :{}, avg score : {}".format(n_epi, score/print_interval))
            if score/print_interval > max_score:
                torch.save(pi.state_dict(), 'model_weights.pth')
                print(f"# max avg balance : {1000 + score/print_interval}, and save model_weights.pth")
                max_score = score/print_interval
            score = 0.0
        if eps >= 0:
            eps = eps - 0.01

    env.close()

In [12]:
if __name__ == '__main__':
    main()

/usr/local/lib/python3.10/dist-packages/gym/core.py:317: DeprecationWarning: WARN: Initializing wrapper in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(
/usr/local/lib/python3.10/dist-packages/gym/wrappers/step_api_compatibility.py:39: DeprecationWarning: WARN: Initializing environment in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(
/usr/local/lib/python3.10/dist-packages/gym/utils/passive_env_checker.py:141: UserWarning: WARN: The obs returned by the `reset()` method was expecting numpy array dtype to be float64, actual type: float32
  logger.warn(
/usr/local/lib/python3.10/dist-packages/gym/utils/passive_env_checker.py:165: UserWarning: WARN: The obs returned by the `reset()` method is not within the observation space.
  

# of episode :10, avg score : 103.71762138970664
# max score : 103.71762138970664, and save model_weights.pth
# of episode :20, avg score : 103.71293821869361
# of episode :30, avg score : 103.21428699861401
# of episode :40, avg score : 103.47871003333562
# of episode :50, avg score : 103.05581585486148
# of episode :60, avg score : 103.75117096299114
# max score : 103.75117096299114, and save model_weights.pth
# of episode :70, avg score : 102.54662084674324
# of episode :80, avg score : 103.21943043417018
# of episode :90, avg score : 103.64274866837597
# of episode :100, avg score : 103.21813451051828
# of episode :110, avg score : 102.96882294691093
# of episode :120, avg score : 102.96052764318213
# of episode :130, avg score : 102.97046572794707
# of episode :140, avg score : 102.61062571850547
# of episode :150, avg score : 103.6536615240278
# of episode :160, avg score : 103.34337647974746


KeyboardInterrupt: ignored

# STEP. Render

In [8]:
def model_render(env_name, **kwargs):
    env = gym.make(env_name, **kwargs)
    episode_trigger=lambda e: True  # all Episode Recode

    env = gym.wrappers.RecordVideo(env, "./video", episode_trigger=episode_trigger, video_length=100000)

    for episode in range(1):
        s = env.reset()
        done = False
        score = 0

        pi = Policy()
        pi.load_state_dict(torch.load('model_weights.pth'))
        pi.eval()

        pi.to(device)

        while not done:
            prob = pi(torch.from_numpy(s).float().to(device))
            m = Categorical(prob)
            a = m.sample()
            s_prime, r, done, info = env.step(a.item())
            done_mask = 0.0 if done else 1.0
            s = s_prime
            score += r

        print(f"# of episode {episode}:, avg score : {score}")
    env.close()

In [9]:
model_render("gym_examples:TradeWorld-v0", df=df, df_render=df_render, obs_len=180)

/usr/local/lib/python3.10/dist-packages/gym/wrappers/record_video.py:78: UserWarning: WARN: Overwriting existing videos at /content/video folder (try specifying a different `video_folder` for the `RecordVideo` wrapper if this is not desired)
  logger.warn(
/usr/local/lib/python3.10/dist-packages/gym/wrappers/monitoring/video_recorder.py:78: DeprecationWarning: WARN: Recording ability for environment TradeWorld-v0 initialized with `render_mode=None` is marked as deprecated and will be removed in the future.
  logger.deprecation(
/usr/local/lib/python3.10/dist-packages/gym/core.py:43: DeprecationWarning: WARN: The argument mode in render method is deprecated; use render_mode during environment initialization instead.
See here for more information: https://www.gymlibrary.ml/content/api/
  deprecation(
/usr/local/lib/python3.10/dist-packages/gym/utils/passive_env_checker.py:141: UserWarning: WARN: The obs returned by the `step()` method was expecting numpy array dtype to be float64, actual

# of episode 0:, avg score : 3.3188810380014266


In [10]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open('./video/rl-video-episode-0.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=500 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)